In [1]:
from mars.utils import set_root_path
import pandas as pd


import os
os.chdir('../..')

In [2]:
pd.set_option('max_colwidth', -1)

d = pd.read_csv("cluster_stats.csv")


d.sort_values(by=['n_outliers'])

/var/folders/43/n960f0n91p92c4kkr882m6fm0000gn/T/ipykernel_2729/4240234482.py:1: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('max_colwidth', -1)


Unnamed: 0  \
5  5            
4  4            
7  7            
9  9            
8  8            
6  6            
0  0            
2  2            
1  1            
3  3            

                                                                                                         name  \
5  big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0_min_samples_15.parquet                                             
4  reduced_300_big_cleaned_mini_all-MiniLM-L6-v2_min_clust_size_3_min_samples_3_eps_0.0_min_samples_3.parquet   
7  reduced_300_big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0.parquet                                                
9  reduced_200_big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0.parquet                                                
8  reduced_100_big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0.parquet                                                
6  big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0_min_samples_5.parquet                                              
0  big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0_min_samples_7.parquet                                              
2  big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0_min_samples_9.parquet                                              
1  big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0_min_samples_11.parquet                                             
3  big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0_min_samples_13.parquet                                             

   n_clusters  n_outliers  mean_cluster_size  
5  4           174736      43684.000000       
4  212434      1092745     5.143927           
7  90157       1215995     13.487527          
9  92154       1240632     13.462595          
8  116500      1581920     13.578712          
6  54328       3066769     56.449142          
0  32608       3287774     100.827220         
2  23181       3392493     146.348001         
1  18240       3463119     189.863980         
3  14901       3503691     235.131266

In [3]:
CLUSTERS_FILE = 'reduced_300_big_cleaned_mini_all-MiniLM-L6-v2_eps_0.0.parquet'

In [4]:
merged_data_path = "data/s2orc/clean_merged.parquet"

if not os.path.exists(merged_data_path):
    df = pd.read_parquet('data/s2orc/processed_big.parquet')
    df2 = pd.read_parquet('data/s2orc/big_ai_dataset_with_affiliations.parquet')
    dff = pd.merge(df2, df[['paper_id','noun_chunks_cleaned']], on='paper_id', how='left')
    #df2 = df2[df2['institutions'].str.len()!=0]
    dff['inbound_citations'] = dff['inbound_citations'].apply(lambda ids: [int(id) for id in ids])
    dff['outbound_citations'] = dff['outbound_citations'].apply(lambda ids: [int(id) for id in ids])

    dff = dff[~dff['noun_chunks_cleaned'].isna()]
    dff.to_parquet(merged_data_path)
else:
    print("Loading...")
    dff = pd.read_parquet(merged_data_path)

Loading...


In [5]:
def make_chunk_to_meme_id(df_clusters)->dict:
    """Map all chunks to their meme id, dependent on cluster. Outliers are given new ids."""
    next_id = max(df_clusters['cluster'])+1
    chunk_to_meme_id=dict()
    for _, r in df_clusters.iterrows():
        id = r['cluster']
        if id==-1:
            id = next_id
            next_id += 1
        chunk_to_meme_id[r['chunk']] = id
    return chunk_to_meme_id

In [6]:
# map chunks to clusters
df_clusters = pd.read_parquet('data/s2orc/clusterings/'+CLUSTERS_FILE, columns=['chunk', 'cluster'])
print("loaded!")
chunk_to_meme = make_chunk_to_meme_id(df_clusters)
dff['memes'] = dff['noun_chunks_cleaned'].apply(lambda chunks: list(map(chunk_to_meme.get, chunks)))

loaded!


In [7]:
dff.index = dff['paper_id']

def get_inbound_memes(ids):
    memes = []
    for id in ids:
        try:
            for meme in dff['memes'][id]:
                memes.append(meme)
        except KeyError:
            pass
    return memes

In [8]:
dff['inbound_memes']=dff['inbound_citations'].apply(get_inbound_memes)

In [9]:
dff['inbound_memes'].str.len()

paper_id
199668001    0  
2879234      888
17786914     42 
17432300     154
8392651      259
            ... 
6048192      147
11619477     58 
5807289      45 
15894398     29 
15895702     45 
Name: inbound_memes, Length: 394897, dtype: int64

In [10]:
import plotly.express as px

px.histogram(dff['inbound_memes'].str.len(), log_y=True)

In [11]:
df_out = dff[['paper_id', 'outbound_citations','inbound_citations','institutions','countries','types','unique_institutions','is_big_tech','noun_chunks_cleaned','memes', 'inbound_memes']]

In [55]:
os.makedirs('data/s2orc/results/', exist_ok=True)
df_out.to_parquet('data/s2orc/results/'+CLUSTERS_FILE)

In [15]:
pd.DataFrame(chunk_to_meme.items(), columns=['chunk','meme_id'])ś

chunk  meme_id
0                                            90157  
1        correspond textual comment          90158  
2        both aesthetic sensibility          36590  
3        new amino acid encoding scheme      88493  
4        actual task execution               54040  
...                        ...                 ...  
3883762  single random value                 45034  
3883763  employ class hierarchy              35154  
3883764  voluntary task choice               1306150
3883765  multi channel convolutional neural  68691  
3883766  virtual reality interaction         1306151

[3883767 rows x 2 columns]